In [1]:
import pandas as pd
from bs4 import BeautifulSoup
from pprint import pprint
import time
import math
import yaml
import pickle
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support import expected_conditions
from selenium.webdriver.support.wait import WebDriverWait

In [2]:
with open("../config.yaml", "r") as f:
    CFG = yaml.safe_load(f)

In [3]:
class Crawler():
    def __init__(self, url):
        self.driver = webdriver.Chrome()
        self.driver.get(url)
        self.driver.set_window_size(1280, 680)
        time.sleep(5)

    def teardown_method(self):
        self.driver.quit()

    def select_execute_element(self, selector, value, sleep_time):
        button =  self.driver.find_element(selector, value)
        self.driver.execute_script("arguments[0].click();", button)
        time.sleep(sleep_time)

    def get_iters(self):
        total = self.driver.find_element(By.CSS_SELECTOR, ".sbcd-total")
        total = total.text
        self.iters = math.ceil((int(total)-50) / 50)

    def exponential_growth(
        self, initial_delay, growth_factor, max_delay, iter
        ):
        return min(initial_delay * (1 + growth_factor) ** iter, max_delay)
        
    def run(self):
        self.get_iters()
        self.select_execute_element(By.CSS_SELECTOR, ".sbcd-filters-title", 0.5)
        self.select_execute_element(By.CSS_SELECTOR, ".sbcd-filter-reset", 2)
        self.select_execute_element(By.CSS_SELECTOR, ".sbcd-filters-title", 0.2)
        
        for x in range(10):#range(self.iters):
            sleeptime = self.exponential_growth(0.1, 0.001, 10, x)
            self.select_execute_element(By.CSS_SELECTOR, ".sbcd-next", sleeptime)

        self.page_source =  self.driver.page_source
        pickle.dump(self.page_source, open('page_source.pkl', 'wb'))

    def parse_pagesource(self, page_source):
        soup = BeautifulSoup(page_source, 'html.parser')
        table = soup.find('table')
        
        df = pd.DataFrame(
            columns=[
                'Date', 'SITE', 'CITY/TOWN', 'EXPECTED SUBSTANCE',
                'FENTANYL TEST STRIP', 'BENZO TEST STRIP', 'FTIR SPECTROMETER'
            ]
        )
        for row in table.tbody.find_all('tr'):    
            # Find all data for each column
            columns = row.find_all('td')
            
            if(columns != []):
                DATE = columns[0].text.strip()
                SITE = columns[1].text.strip()
                CITY_TOWN = columns[2].text.strip()
                EXPECTED_SUBSTANCE = columns[3].text.strip()
                FENTANYL_TEST_STRIP = columns[4].text.strip()
                BENZO_TEST_STRIP = columns[5].text.strip()
                FTIR_SPECTROMETER = columns[6].text.strip()

                df = df.append({
                    'DATE': DATE,  'SITE': SITE,
                    'CITY/TOWN': CITY_TOWN,
                    'EXPECTED SUBSTANCE': EXPECTED_SUBSTANCE,
                    'FENTANYL TEST STRIP': FENTANYL_TEST_STRIP,
                    'BENZO TEST STRIP': BENZO_TEST_STRIP,
                    'FTIR SPECTROMETER': FTIR_SPECTROMETER
                    }, ignore_index=True)
        return df

In [4]:
crawler = Crawler(CFG['URL'])
crawler.run()

In [6]:
df = crawler.parse_pagesource(crawler.page_source)
df

C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated

Date                             SITE  CITY/TOWN     EXPECTED SUBSTANCE  \
0   NaN            Outreach Urban Health    Kelowna  Down (Unknown Opioid)   
1   NaN        Burdock House (Penticton)  Penticton          Crack Cocaine   
2   NaN            Get Your Drugs Tested  Vancouver                Unknown   
3   NaN            Get Your Drugs Tested  Vancouver                    GHB   
4   NaN                           Insite  Vancouver        Methamphetamine   
..  ...                              ...        ...                    ...   
95  NaN            Get Your Drugs Tested  Vancouver                Unknown   
96  NaN            Get Your Drugs Tested  Vancouver                   MDMA   
97  NaN            Get Your Drugs Tested  Vancouver       4-Fluorophenibut   
98  NaN  Cammy LaFleur Outreach (Vernon)     Vernon        Methamphetamine   
99  NaN  Cammy LaFleur Outreach (Vernon)     Vernon        Methamphetamine   

   FENTANYL TEST STRIP BENZO TEST STRIP  \
0             Positive         Positive   
1             Negative              N/A   
2             Negative         Negative   
3             Negative              N/A   
4             Negative              N/A   
..                 ...              ...   
95            Positive         Positive   
96            Negative              N/A   
97            Negative              N/A   
98            Negative              N/A   
99            Negative              N/A   

                                    FTIR SPECTROMETER        DATE  
0                          ErythritolCaffeineFentanyl  2022-11-30  
1                                        Cocaine Base  2022-11-30  
2                                  MDAUncertain Match  2022-11-30  
3                            GHB (Wet)Uncertain Match  2022-11-30  
4                     MethamphetamineDimethyl Sulfone  2022-11-30  
..                                                ...         ...  
95  para-FluorofentanylCaffeineErythritolMethamphe...  2022-11-29  
96                                               MDMA  2022-11-29  
97                                   No Library Match  2022-11-29  
98                                    Methamphetamine  2022-11-29  
99                                    Methamphetamine  2022-11-29  

[100 rows x 8 columns]

In [19]:
page_source = pickle.load(open('page_source.pkl', 'rb'))
crawler = Crawler(CFG['URL'])
crawler.parse_pagesource(page_source)

C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated

In [17]:
soup = BeautifulSoup(crawler.page_source, 'html.parser')
table = soup.find('table')

df = pd.DataFrame(
    columns=[
        'Date', 'SITE', 'CITY/TOWN', 'EXPECTED SUBSTANCE',
        'FENTANYL TEST STRIP', 'BENZO TEST STRIP', 'FTIR SPECTROMETER'
    ]
)
for row in table.tbody.find_all('tr'):    
    # Find all data for each column
    columns = row.find_all('td')
    
    DATE = columns[0].text.strip()
    SITE = columns[1].text.strip()
    CITY_TOWN = columns[2].text.strip()
    EXPECTED_SUBSTANCE = columns[3].text.strip()
    FENTANYL_TEST_STRIP = columns[4].text.strip()
    BENZO_TEST_STRIP = columns[5].text.strip()
    FTIR_SPECTROMETER = columns[6].text.strip()

    df = df.append({'DATE': DATE, 'SITE': SITE, 'CITY/TOWN': CITY_TOWN, 'EXPECTED SUBSTANCE': EXPECTED_SUBSTANCE, 'FENTANYL TEST STRIP': FENTANYL_TEST_STRIP, 'BENZO TEST STRIP': BENZO_TEST_STRIP, 'FTIR SPECTROMETER': FTIR_SPECTROMETER}, ignore_index=True)

C:\Users\broug\AppData\Local\Temp\ipykernel_17976\2070173647.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'DATE': DATE, 'SITE': SITE, 'CITY/TOWN': CITY_TOWN, 'EXPECTED SUBSTANCE': EXPECTED_SUBSTANCE, 'FENTANYL TEST STRIP': FENTANYL_TEST_STRIP, 'BENZO TEST STRIP': BENZO_TEST_STRIP, 'FTIR SPECTROMETER': FTIR_SPECTROMETER}, ignore_index=True)
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\2070173647.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'DATE': DATE, 'SITE': SITE, 'CITY/TOWN': CITY_TOWN, 'EXPECTED SUBSTANCE': EXPECTED_SUBSTANCE, 'FENTANYL TEST STRIP': FENTANYL_TEST_STRIP, 'BENZO TEST STRIP': BENZO_TEST_STRIP, 'FTIR SPECTROMETER': FTIR_SPECTROMETER}, ignore_index=True)
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\2070173647.py:22: FutureWarning: The fra

In [8]:
soup.text

"\n\n\n\n\n\n\n\n\n     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nResults Table - BCCSU Drug Checking\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\xad\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n  \n \n\n\n\n\n\n\n\n\n\n\n\n\n\n \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n  \n\n\n \n About\n\nHow it Works\nOverview of Technologies\nVideo\nFAQs\nEvaluation\nFunders and Partners\nContact\n\n\nDrug Checking Results\n\nDashboard\nAbout This Data\nResults Table\n\n\nLocations\n\nFraser Health\nInterior Health\nIsland Health\nNorthern Health\nVancouver Coastal Health\n\n\nDrug Alerts\n\nCurrent Drug Checking Alerts\nPast Drug Checking Alerts\n\n\nResources\n\nMonthly Drug Checking Reports\nCommunity Resources\nManuals and Guidelines\nBCCSU FTIR-ATR Library\nReports\n\n\nTraining\n  \n\n\n\n\nResults Table\n\n\n\n\n\n\n\n\nBCCSU Sites > BCCSU Drug Checking > Results Table \n\n\n\n\n\n\n\n\n\nHave you seen our new DrugSense Dashboard? \nDive deep into drug checking results from

In [9]:
crawler.page_source

'<html dir="ltr" lang="en-US" prefix="og: https://ogp.me/ns#" class=" js flexbox flexboxlegacy canvas canvastext webgl no-touch geolocation postmessage websqldatabase indexeddb hashchange history draganddrop websockets rgba hsla multiplebgs backgroundsize borderimage borderradius boxshadow textshadow opacity cssanimations csscolumns cssgradients cssreflections csstransforms csstransforms3d csstransitions fontface generatedcontent video audio localstorage sessionstorage webworkers no-applicationcache svg inlinesvg smil svgclippaths"><head>\n\t\n\n\t<meta http-equiv="Content-Type" content="text/html; charset=utf-8">\n        <!--// SITE META //-->\n    <meta charset="UTF-8">\n    <!-- Mobile Specific Metas\n    ================================================== -->\n\t\t\t                <meta name="viewport" content="width=device-width, user-scalable=no, initial-scale=1.0, minimum-scale=1.0">\n                <meta name="format-detection" content="telephone=no">\n\t    \t<!--// PINGBACK

In [13]:
for row in table.tbody.find_all('tr'):
    print()

[<td class="date" data-title="Date">2022-11-30</td>, <td class="location" data-title="Site">Outreach Urban Health</td>, <td class="city" data-title="City/Town">Kelowna</td>, <td class="drug" data-title="Expected Substance">Down (Unknown Opioid)</td>, <td class="fent_strip_test" data-title="Fentanyl Test Strip">Positive</td>, <td class="benzo_strip_test" data-title="Benzo Test Strip">Positive</td>, <td class="ftir_spec_group" data-title="FTIR Spectrometer">Erythritol<br/>Caffeine<br/>Fentanyl</td>]


In [19]:
len(table.tbody.find_all('tr'))

100